In [7]:
import json

In [4]:
# with open("./HumanEval/HumanEval.jsonl") as f:
#     data = f.readlines()
#     data = [json.loads(line) for line in data]
#     for item in data:
#         file_name = item['task_id'].split('/')[-1]
#         with open('./HumanEval/Files/' + file_name + '.py', 'w') as f:
#             f.write(item['prompt'])
            

In [3]:
with open("./HumanEval.jsonl") as f:

    data = f.readlines()
    data = [json.loads(line) for line in data]
    for i in range(len(data)):
        item = data[i]
        file_name = item['task_id'].split('/')[-1]
        with open('./HumanEval/Files/' + file_name + '.py', 'r') as f:
            data[i]['canonical_solution'] = f.read()
            prompt = "\"\"\"".join(data[i]['canonical_solution'].split("\"\"\"")[:-1])
            data[i]['prompt'] = prompt.lstrip()+ "\"\"\""


In [92]:
with open("./HumanEval_Clear.jsonl", 'w') as f:
    for item in data:
        f.write(json.dumps(item) + '\n')

In [93]:
def count_indent(text: str) -> int:
    # print(len(text))
    count = 0
    for char in text:
        # print(ord(char))
        if char == " ":
            count += 1
        # elif char == "\t":
        #     count += 4
        else:
            break
    return count


def fix_indents(text: str, multiple: int = 4):
    outputs = []
    for line in text.split("\n"):
        line = line.replace("\t", "    ")
        
        while count_indent(line) % multiple != 0:
            # print(count_indent(line))
            mod = count_indent(line) % multiple
            line = line[mod:]
        outputs.append(line)
    return "\n".join(outputs)


print(fix_indents("""
from typing import List

def has_close_elements(numbers: List[float], threshold: float) -> bool:      
    
    \"\"\"
      Check if, in a given list of numbers, any two numbers are closer to each other than the      given threshold.           >>> has_close_elements([1.0, 2.0, 3.0], 0.5)      False      >>> has_close_elements([1.0, 2.8, 3.0, 4.0, 5.0, 2.0], 0.3)      True      
    \"\"\"

      # Your code here
      return True
    """))



from typing import List

def has_close_elements(numbers: List[float], threshold: float) -> bool:      
    
    """
    Check if, in a given list of numbers, any two numbers are closer to each other than the      given threshold.           >>> has_close_elements([1.0, 2.0, 3.0], 0.5)      False      >>> has_close_elements([1.0, 2.8, 3.0, 4.0, 5.0, 2.0], 0.3)      True      
    """

    # Your code here
    return True
    


In [94]:
def filter_code(completion: str) -> str:
    completion = completion.lstrip("\n")
    return completion.split("\n\n")[0]

In [97]:
with open("./humaneval_original_Salesforce_codegen-2B-mono_predictions.jsonl") as f:

    pred_data = f.readlines()
    pred_data = [json.loads(line) for line in pred_data]
len(pred_data)

new_data = []
for item in pred_data:
    task_id = item['task_id']
    for i in range(len(data)):
        if data[i]['task_id'] == task_id:
            entry_point = data[i]['entry_point']
            original_code = item['completion']
          
            index = original_code.find(entry_point)
            part_prompt = original_code[:index]
            code = original_code[index:]
            print(code)
            print("--"*100)
            clear_code = filter_code(code)

            original_code = part_prompt+ clear_code
            original_code = original_code.replace("\"\"\"", "\n\t\"\"\"\n")
            # original_code = original_code.replace("      ", "\t")
            # original_code = original_code.replace("\t  ", "\t\t")
            original_code = fix_indents(original_code)

            # Fix indents
            # original_code = original_code.replace("\n", "\n\t")

            # original_code = fix_indents(original_code)
            item['completion'] = original_code
            print(original_code)
            print("--"*100)

            new_data.append(item)

has_close_elements(numbers: List[float], threshold: float) -> bool:      """ Check if in given list of numbers, are any two numbers closer to each other than      given threshold.      >>> has_close_elements([1.0, 2.0, 3.0], 0.5)      False      >>> has_close_elements([1.0, 2.8, 3.0, 4.0, 5.0, 2.0], 0.3)      True      """
      for i in range(len(numbers) - 1):
          if abs(numbers[i] - numbers[i+1]) <= threshold:
              return True
      return False

def has_close_elements_v2(numbers: List[float], threshold: float) -> bool:
      """ Check if in given list of numbers, are any two numbers closer to each other than      given threshold.      >>> has_close_elements([1.0, 2.0, 3.0], 0.5)      False      >>> has_close_elements([1.0, 2.8, 3.0, 4.0, 5.0, 2.0], 0.3)      True      """
      for i in range(len(numbers) - 1):
          if abs(numbers[i] - numbers[i+1]) <= threshold:
              return True
      return False

def has_close_elements_v3(numbers: List[float], thresh

In [98]:
with open("./humaneval_original_Salesforce_codegen-2B-mono_predictions_cleared.jsonl", 'w') as f:
    for item in new_data:
        f.write(json.dumps(item) + '\n')